In [ ]:
### Test mciro-manager and PVCAM live

In [1]:
import os
os.chdir('../')

import connect as connect
import chip
import position as pos
import goto
from pyvcam import pvc
from pyvcam.camera import Camera
from matplotlib import pyplot as plt
import MMCorePy
import time
import math

import sys
sys.path.insert(0, '../miq_p3')
import miq

i = 0
os.chdir('focus_data_generator')

Instructions for updating:
Use the retry module or similar alternatives.


In [2]:
# Create the Position Lists
corners_pl = pos.PositionList()
z16_pl = pos.PositionList()

In [3]:
mmc = MMCorePy.CMMCore()
mmc.getVersionInfo()
# mmc.loadDevice('Scope', 'LeicaDMI', 'Scope')
# mmc.initializeAllDevices()
print ("Devices loaded from config file:\n", mmc.getLoadedDevices())

CMMError: Error in device "Scope": (Error message unavailable) (10016)

In [53]:
# Connect micro-manager
mmc = MMCorePy.CMMCore()
# Load Scope Config from file
mmc.loadSystemConfiguration("../MMConfig_YellenLab_ubuntu.cfg")
print ("Devices loaded from config file:\n", mmc.getLoadedDevices())
print ("\n Stage at: (", mmc.getXPosition(), ",", mmc.getYPosition(), ")")

xyStage = mmc.getXYStageDevice()
# Need to set this 

zStage = mmc.setFocusDevice('FocusDrive')

Devices loaded from config file:
 ('/dev/ttyUSB1', '/dev/ttyUSB0', 'Scope', 'IL-Turret', 'ObjectiveTurret', 'TL-FieldDiaphragm', 'IL-FieldDiaphragm', 'IL-ApertureDiaphragm', 'FocusDrive', 'MagnificationChanger', 'SidePort', 'IL-Shutter', 'TL-Shutter', 'XYStage', 'Transmitted Light', 'XYStage-1', 'Core')

 Stage at: ( -52.4 , -7214.1 )


In [4]:
# Make sure that PVCAM is working
pvc.init_pvcam()
cam = next(Camera.detect_camera())
print(cam)
pvc.uninit_pvcam()

pvcamUSB_0


True

In [8]:
# Show an image from the PVCAM
pvc.init_pvcam()
cam = next(Camera.detect_camera())
cam.open()

frame = cam.get_frame(exp_time=1).reshape(cam.sensor_size[::-1])
plt.axhline(math.floor(cam.sensor_size[1]/2), color='r', linewidth=3.0)
plt.axvline(math.floor(cam.sensor_size[0]/2), color='r', linewidth=3.0)
plt.rcParams['figure.figsize'] = [150, 150]
plt.imshow(frame, cmap="gray")
#plt.savefig('data/img'+str(i)+'.png')
i = i+1
time.sleep(1)

print(cam.sensor_size[0])
print(cam.sensor_size[1])


cam.close()
pvc.uninit_pvcam()

RuntimeError: Init_pvcam has been called twice without closing (C2_PVCAM_ALREADY_INITED)

In [4]:
cam.close()

RuntimeError: Failed to close camera.

In [13]:
# Show an image from the PVCAM
pvc.init_pvcam()
cam2 = next(Camera.detect_camera())
cam2.open()

RuntimeError: Failed to open camera.

In [7]:
frame = cam2.get_frame(exp_time=1).reshape(cam2.sensor_size[::-1])
plt.imshow(frame, cmap="gray")

In [12]:
pvc.uninit_pvcam()

True

In [ ]:
### Create the Position List for the Z dataset

In [ ]:
## Align three Corners

In [4]:
def addCorner():
    ''' 
    Adds a position to the corners_pl positionlist
    '''
    if corners_pl.getNumberOfPositions() > 2:
        print("corners_pl already has 3 corners")
        return
    X = -mmc.getXPosition()
    Y = mmc.getYPosition()
    Z = mmc.getPosition()
    print("X = " + str(X))
    print("Y = " + str(Y))
    print("Z = " + str(Z))
    msp = pos.MultiStagePosition(xyStage='xyStage', 
                                 x=X, 
                                 y=Y, 
                                 zStage='zStage', 
                                 z=Z)
    corners_pl.addPosition(pos=msp)

In [7]:
# Move stage to each corner and run this 
# block at each - use display block to 
# align to corner (Should only run 3 times)
addCorner()
print(corners_pl.positions)

X = 1525.9
Y = -7978.0
Z = 357476148144.511
[<position.MultiStagePosition object at 0x7ff0a8464ac8>, <position.MultiStagePosition object at 0x7ff0a8464c50>, <position.MultiStagePosition object at 0x7ff108de25f8>]


In [8]:
# Get the chip params
chip_params = chip.Chip("M chip", corners_pl)
# Get the Periods, normals, as sin/cos for the chip
periodX, periodY = chip_params.get_periods()
nx, ny, nz = chip_params.get_normals()
cosx = chip_params.get_cosX()
sinx = chip_params.get_sinX()
print("Array Period X =" + str(periodX))
print("Array Period Y =" + str(periodY))

Array Period X =202.84921875
Array Period Y =200.17234042553193


In [9]:
pl = chip_params.get_focus_xy_points(4,4)

DeltaX =  5798.377777777777
DeltaY =  -2111.577777777778
i,j =  0 , 0
NEW =  4348.783333333334 , -1583.6833333333334
4348.783333333334 , -1583.6833333333334
i,j =  1 , 0
NEW =  10147.16111111111 , -1583.6833333333334
10147.16111111111 , -1583.6833333333334
i,j =  2 , 0
NEW =  15945.538888888888 , -1583.6833333333334
15945.538888888888 , -1583.6833333333334
i,j =  3 , 0
NEW =  21743.916666666664 , -1583.6833333333334
21743.916666666664 , -1583.6833333333334
i,j =  0 , 1
NEW =  4348.783333333334 , 527.8944444444446
4348.783333333334 , 527.8944444444446
i,j =  1 , 1
NEW =  10147.16111111111 , 527.8944444444446
10147.16111111111 , 527.8944444444446
i,j =  2 , 1
NEW =  15945.538888888888 , 527.8944444444446
15945.538888888888 , 527.8944444444446
i,j =  3 , 1
NEW =  21743.916666666664 , 527.8944444444446
21743.916666666664 , 527.8944444444446
i,j =  0 , 2
NEW =  4348.783333333334 , 2639.4722222222226
4348.783333333334 , 2639.4722222222226
i,j =  1 , 2
NEW =  10147.16111111111 , 2639.47222222

In [11]:
goto.get_focus(pl, mmc, 7)

INFO:tensorflow:Restoring parameters from ./model.ckpt-1000042
(array([0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.00120192, 0.00120192, 0.08894231,
       0.90865385]), array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10]), 9.905048076923077)


NameError: name 'prediction' is not defined

In [59]:
starting_z_value = mmc.getPosition()
print ("Starting z: ", starting_z_value)

# Get focus model
focus_model = miq.get_classifier()

# Start Camera
pvc.init_pvcam()
cam = next(Camera.detect_camera())
cam.open()
cam.clear_mode = 'Never'
cam.exp_mode = "Ext Trig Trig First"
cam.readout_port = 0
cam.speed_table_index = 0
cam.gain = 1

last_predit = -1
direction = 1
iters = 0 
z_step = 7
while True:
    frame = cam.get_frame(exp_time=1).reshape(cam.sensor_size[::-1])
    prediction = focus_model.score(frame)[2]
    print (prediction)
    
    if prediction < 1.9:
        print ('Done')
        break
    elif (not (last_predit == -1)) and prediction < last_predit:
        ''' Focus is getting better, keep going in same direction '''
        new_z = starting_z_value + direction*z_step
        print ('1', new_z)
        mmc.setPosition(new_z)
        mmc.waitForSystem()
    elif (not (last_predit == -1)) and prediction > last_predit:
        ''' Focus is getting worse, move in opposite direction '''
        direction = -direction
        new_z = starting_z_value + direction*z_step
        print('2', new_z)
        mmc.setPosition(new_z)
        mmc.waitForSystem()
    else:
        ''' We do not have a previous direction - move one step in 
            the +z direction 
        '''
        print('3', new_z)
        new_z = starting_z_value + z_step
        mmc.setPosition(new_z)
        mmc.waitForSystem()
        
    starting_z_value = new_z
    last_predit = prediction
    iters = iters +1
    if iters == 10:
        # Something went wrong
        print ('Could not find focus')
        break
        
cam.close()
pvc.uninit_pvcam()

Starting z:  357476148205.9836
INFO:tensorflow:Restoring parameters from ./model.ckpt-1000042
7.2199519230769225
3 357476148181.8022
8.286057692307693
2 357476148205.9836
7.1862980769230775
1 357476148198.9836
5.007211538461538
1 357476148191.9836
3.3004807692307696
1 357476148184.9836
1.9663461538461537
1 357476148177.9836
1.735576923076923
Done


True

In [55]:
pvc.uninit_pvcam()

True

In [17]:
my_goto = goto.Goto(mmc, pl, 'data')

In [19]:
my_goto.image_z_stack_pos_list()

In [32]:
mmc.getFocusDevice()

'FocusDrive'

In [33]:
mmc.getXYStageDevice()

'XYStage-1'

In [34]:
mmc.getPosition()

357476148144.511

In [35]:
mmc.getPosition()

357476148144.511

In [51]:
mmc.setPosition(357476148127.511)
mmc.waitForSystem()

CMMError: Error in device "FocusDrive": Serial command failed.  Is the device connected to the serial port? (14)

In [2]:
from pyvcam import pvc
from pyvcam.camera import Camera
import pylab as pl
import time
import cv2
from matplotlib import pyplot as plt
import math

In [3]:
pvc.init_pvcam()
cam = next(Camera.detect_camera())
cam.open()

print ("Camera started")
cam.clear_mode = "Never"
cam.exp_mode = "Ext Trig Trig First"
cam.readout_port = 0
cam.speed_table_index = 0
cam.gain = 1

#cam.start_live(exp_time=1)

Camera started


In [7]:
import scipy.misc
frame = cam.get_frame(exp_time=1).reshape(cam.sensor_size[::-1])
scipy.misc.imsave('outfile.tif', frame)



/home/cellcounter/miniconda2/envs/Py36/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: `imsave` is deprecated!
`imsave` is deprecated in SciPy 1.0.0, and will be removed in 1.2.0.
Use ``imageio.imwrite`` instead.
  This is separate from the ipykernel package so we can avoid doing imports until


In [9]:
import imageio
# imageio.imwrite('imwrite.tif', frame)

In [10]:
frame = cam.get_frame(exp_time=1).reshape(cam.sensor_size[::-1])
#plt.axhline(math.floor(cam.sensor_size[1]/2), color='r', linewidth=3.0)
#plt.axvline(math.floor(cam.sensor_size[0]/2), color='r', linewidth=3.0)
#plt.rcParams['figure.figsize'] = [100, 100]
# plt.imshow(frame, cmap="gray")
# plt.savefig('test2.tif')

In [11]:
import tifffile as tif
tif.imwrite('temp1.tif', frame)

In [29]:
def increase_brightness(frame, value=30):
    img = cv2.imread(frame)
    hsv = cv2.cvtColor(img, cv2.COLOR_BGR2HSV)
    h, s, v = cv2.split(hsv)

    lim = 255 - value
    v[v > lim] = 255
    v[v <= lim] += value

    final_hsv = cv2.merge((h, s, v))
    img = cv2.cvtColor(final_hsv, cv2.COLOR_HSV2BGR)
    return img

width = 800
height = int(cam.sensor_size[1] * width / cam.sensor_size[0])
dim = (width, height)

while True:
    time.sleep(2)
    frame = cam.get_live_frame().reshape(cam.sensor_size[::-1])
    #frame = cam.get_frame(exp_time=1).reshape(cam.sensor_size[::-1])
    #frame = increase_brightness(frame)
    frame = cv2.resize(frame,dim, interpolation = cv2.INTER_AREA)
    #cv2.line(frame, (int(width/2), 0), (int(width/2), height), (255,255,255), 1)
    #cv2.line(frame, (0, int(height/2)), (width, int(height/2)), (255,255,255), 1)

    cv2.imshow('Live Mode', frame)

    if cv2.waitKey(10) == 27:
        break
    


ValueError: Invalid parameters.

In [12]:
# cam.close()
pvc.uninit_pvcam()

True